2. IMDB 리뷰 토큰화하기

In [1]:
import sentencepiece as spm
import pandas as pd
import urllib.request
import csv

In [2]:
urllib.request.urlretrieve("https://raw.githubusercontent.com/LawrenceDuan/IMDb-Review-Analysis/master/IMDb_Reviews.csv", filename="IMDb_Reviews.csv")

('IMDb_Reviews.csv', <http.client.HTTPMessage at 0x2b4fbe9ed60>)

In [3]:
train_df = pd.read_csv('IMDb_Reviews.csv')
train_df['review']

0        My family and I normally do not watch local mo...
1        Believe it or not, this was at one time the wo...
2        After some internet surfing, I found the "Home...
3        One of the most unheralded great works of anim...
4        It was the Sixties, and anyone with long hair ...
                               ...                        
49995    the people who came up with this are SICK AND ...
49996    The script is so so laughable... this in turn,...
49997    "So there's this bride, you see, and she gets ...
49998    Your mind will not be satisfied by this nobud...
49999    The chaser's war on everything is a weekly sho...
Name: review, Length: 50000, dtype: object

In [4]:
print('리뷰 개수 :',len(train_df)) # 리뷰 개수 출력

리뷰 개수 : 50000


In [7]:
# 센텐스피스의 입력으로 사용하기 위해서 데이터프레임을 txt 파일로 저장

with open('imdb_review.txt', 'w', encoding='utf8') as f:
    f.write('\n'.join(train_df['review']))

In [8]:
# 센텐스피스로 단어 집합과 각 단어에 고유한 정수를 부여

spm.SentencePieceTrainer.Train('--input=imdb_review.txt --model_prefix=imdb --vocab_size=5000 --model_type=bpe --max_sentence_length=9999')

In [9]:
# vocab 생성이 완료되면 imdb.model, imdb.vocab 파일 두개가 생성
# 단어 집합의 크기를 확인하기 위해 vocab 파일을 데이터프레임에 저장

vocab_list = pd.read_csv('imdb.vocab', sep='\t', header=None, quoting=csv.QUOTE_NONE)
vocab_list.sample(10)

0     1
2471   ▁stere -2468
3692     mark -3689
3687     asty -3684
3388     vert -3385
4480     ▁Sus -4477
2319     ▁... -2316
740    ically  -737
3050     ▁cru -3047
1167  ▁stupid -1164
953     ither  -950

In [10]:
# 단어 집합의 크기는 5,000개

len(vocab_list)

5000

In [11]:
# model 파일을 로드

sp = spm.SentencePieceProcessor()
vocab_file = "imdb.model"
sp.load(vocab_file)

True

- encode_as_pieces : 문장을 입력하면 서브 워드 시퀀스로 변환합니다.
- encode_as_ids : 문장을 입력하면 정수 시퀀스로 변환합니다.

In [12]:
lines = [
  "I didn't at all think of it this way.",
  "I have waited a long time for someone to film"
]
for line in lines:
  print(line)
  print(sp.encode_as_pieces(line))
  print(sp.encode_as_ids(line))
  print()

I didn't at all think of it this way.
['▁I', '▁didn', "'", 't', '▁at', '▁all', '▁think', '▁of', '▁it', '▁this', '▁way', '.']
[41, 623, 4950, 4926, 138, 169, 378, 30, 58, 73, 413, 4945]

I have waited a long time for someone to film
['▁I', '▁have', '▁wa', 'ited', '▁a', '▁long', '▁time', '▁for', '▁someone', '▁to', '▁film']
[41, 141, 1364, 1120, 4, 666, 285, 92, 1078, 33, 91]



In [13]:
# GetPieceSize() : 단어 집합의 크기를 확인

sp.GetPieceSize()

5000

In [14]:
# idToPiece : 정수로부터 맵핑되는 서브 워드로 변환

sp.IdToPiece(430)

'▁character'

In [16]:
# PieceToId : 서브워드로부터 맵핑되는 정수로 변환

sp.PieceToId('▁character')

430

In [17]:
# DecodeIds : 정수 시퀀스로부터 문장으로 변환

sp.DecodeIds([41, 141, 1364, 1120, 4, 666, 285, 92, 1078, 33, 91])

'I have waited a long time for someone to film'

In [18]:
# DecodePieces : 서브워드 시퀀스로부터 문장으로 변환

sp.DecodePieces(['▁I', '▁have', '▁wa', 'ited', '▁a', '▁long', '▁time', '▁for', '▁someone', '▁to', '▁film'])

'I have waited a long time for someone to film'

In [19]:
print(sp.encode('I have waited a long time for someone to film', out_type=str))
print(sp.encode('I have waited a long time for someone to film', out_type=int))

['▁I', '▁have', '▁wa', 'ited', '▁a', '▁long', '▁time', '▁for', '▁someone', '▁to', '▁film']
[41, 141, 1364, 1120, 4, 666, 285, 92, 1078, 33, 91]


3. 네이버 영화 리뷰 토큰화하기

In [20]:
urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings.txt", filename="ratings.txt")

('ratings.txt', <http.client.HTTPMessage at 0x2b49b2db790>)

In [22]:
naver_df = pd.read_table('ratings.txt')
naver_df[:5]

id                                           document  label
0   8112052                                어릴때보고 지금다시봐도 재밌어요ㅋㅋ      1
1   8132799  디자인을 배우는 학생으로, 외국디자이너와 그들이 일군 전통을 통해 발전해가는 문화산...      1
2   4655635               폴리스스토리 시리즈는 1부터 뉴까지 버릴께 하나도 없음.. 최고.      1
3   9251303  와.. 연기가 진짜 개쩔구나.. 지루할거라고 생각했는데 몰입해서 봤다.. 그래 이런...      1
4  10067386                        안개 자욱한 밤하늘에 떠 있는 초승달 같은 영화.      1

In [23]:
print('리뷰 개수 :',len(naver_df)) # 리뷰 개수 출력

리뷰 개수 : 200000


In [24]:
# null 값 제거

print(naver_df.isnull().values.any())

True


In [25]:
naver_df = naver_df.dropna(how = 'any') # Null 값이 존재하는 행 제거
print(naver_df.isnull().values.any()) # Null 값이 존재하는지 확인

False


In [26]:
print('리뷰 개수 :',len(naver_df)) # 리뷰 개수 출력

리뷰 개수 : 199992


In [27]:
# 199,992개의 샘플을 naver_review.txt 파일에 저장한 후에 센텐스피스를 통해 단어 집합을 생성

with open('naver_review.txt', 'w', encoding='utf8') as f:
    f.write('\n'.join(naver_df['document']))

In [28]:
spm.SentencePieceTrainer.Train('--input=naver_review.txt --model_prefix=naver --vocab_size=5000 --model_type=bpe --max_sentence_length=9999')

In [29]:
vocab_list = pd.read_csv('naver.vocab', sep='\t', header=None, quoting=csv.QUOTE_NONE)
vocab_list[:10]

0  1
0  <unk>  0
1    <s>  0
2   </s>  0
3     ..  0
4     영화 -1
5    ▁영화 -2
6     ▁이 -3
7     ▁아 -4
8    ... -5
9     ▁그 -6

In [30]:
vocab_list.sample(10)

0     1
4476    숲 -4473
3751    뒤 -3748
4892    궤 -4889
2856  ▁부터 -2853
1490  ▁각본 -1487
523    중에  -520
2570  ▁기본 -2567
3612    져 -3609
3409    랑 -3406
1802   ▁짧 -1799

In [31]:
sp = spm.SentencePieceProcessor()
vocab_file = "naver.model"
sp.load(vocab_file)

True

In [32]:
lines = [
  "뭐 이딴 것도 영화냐.",
  "진짜 최고의 영화입니다 ㅋㅋ",
]
for line in lines:
  print(line)
  print(sp.encode_as_pieces(line))
  print(sp.encode_as_ids(line))
  print()

뭐 이딴 것도 영화냐.
['▁뭐', '▁이딴', '▁것도', '▁영화냐', '.']
[132, 966, 1296, 2590, 3276]

진짜 최고의 영화입니다 ㅋㅋ
['▁진짜', '▁최고의', '▁영화입니다', '▁ᄏᄏ']
[54, 200, 821, 85]



In [33]:
sp.GetPieceSize()

5000

In [34]:
sp.IdToPiece(4)

'영화'

In [35]:
sp.PieceToId('영화')

4

In [36]:
sp.DecodeIds([54, 200, 821, 85])

'진짜 최고의 영화입니다 ᄏᄏ'